In [ ]:
%load_ext autoreload
%autoreload 2

# Open3D Data PreProcessing

In [ ]:
import copy
from lib.render.camera import Camera
import torch
import open3d as o3d
import matplotlib.pyplot as plt
import numpy as np
from tqdm import tqdm
from sklearn.neighbors import KDTree

o3d.utility.set_verbosity_level(o3d.utility.VerbosityLevel.Error)


def visualize(obj):
    o3d.visualization.draw_plotly([obj], up=[0, 1, 0], front=[0.1, 0.1, -0.1])

def visualize_cloud(points, sdfs):
    cloud = o3d.geometry.PointCloud()
    cloud.points = o3d.utility.Vector3dVector(points)
    color = np.zeros_like(points)
    color[sdfs > 0 , 0] = 1
    color[sdfs < 0 , 2] = 1
    cloud.colors = o3d.utility.Vector3dVector(color)
    visualize(cloud)

# Normal Map

## Load And Preprocess

In [ ]:
# path = "/home/borth/sketch2shape/data/shapenet_chair_10/shapes/7e81b5f79e6899cea570c6c691c987a8/model_normalized.obj"
# path = "/home/borth/sketch2shape/data/shapenet_chair_10/shapes/6be6d6ae38d8aca4dc2cbc0befb06e1b/model_normalized.obj"
path = "/home/borth/sketch2shape/data/shapenet_chair_large/shapes/1a6f615e8b1b5ae4dbbc9440457e303e/model_normalized.obj"
mesh = o3d.io.read_triangle_mesh(path)
visualize(mesh)

## Normalize Mesh

In [ ]:
points = np.asarray(mesh.vertices)
translate = (np.min(points, axis=0) + np.max(points, axis=0)) / 2.0
points -= translate
points /= np.linalg.norm(points, axis=-1).max()

# visualzie
mesh.vertices = o3d.utility.Vector3dVector(points)
visualize(mesh)

## Sphere Tracing and Normals Map

In [ ]:
# camera settings
sphere_eps = 1e-01
# sphere_eps = 3
azim, elev, dist = 45, -45, 4
width, height = 256, 256
camera = Camera(azim=azim, elev=elev, dist=dist, sphere_eps=sphere_eps)
points, rays, mask = camera.unit_sphere_intersection_rays()
camera_rays = torch.concatenate([points, rays], dim=-1)

# sphere tracing
cast_rays_mesh = o3d.t.geometry.TriangleMesh.from_legacy(mesh)
scene = o3d.t.geometry.RaycastingScene()
_ = scene.add_triangles(cast_rays_mesh)
ans = scene.cast_rays(camera_rays.numpy())

# noramls map
primitive_normals = ans["primitive_normals"].numpy()

# option 1: flip and range between [0, 1]
# but this does not preserve the norm=1
flip = (primitive_normals * rays.numpy()).sum(axis=-1) > 0
primitive_normals[flip] = -primitive_normals[flip]
surface_mask = ans["t_hit"].numpy() != np.inf
normals = (primitive_normals + 1) / 2
normals[~surface_mask] = 1

# option 2: simple abs value
# normals = np.abs(primitive_normals)

# visualization
plt.imshow(normals.reshape(width, height, 3))

# Sample SDF 

In [ ]:
surface_points = []
surface_normals = []
sphere_eps = 1e-01
width, height = 256, 256
for azim in tqdm(torch.arange(0, 360, 30)):
    for elev in torch.arange(-90, 90, 30):
        # camera settings
        camera = Camera(azim=azim, elev=elev, dist=dist, sphere_eps=sphere_eps)
        points, rays, _ = camera.unit_sphere_intersection_rays()
        points, rays = points.detach().cpu().numpy(), rays.detach().cpu().numpy()
        camera_rays = np.concatenate([points, rays], axis=-1)

        # sphere tracing
        cast_rays_mesh = o3d.t.geometry.TriangleMesh.from_legacy(mesh)
        scene = o3d.t.geometry.RaycastingScene()
        _ = scene.add_triangles(cast_rays_mesh)
        ans = scene.cast_rays(camera_rays)

        # noramls map
        t_hit = ans["t_hit"].numpy()
        mask = t_hit != np.inf

        normals = ans["primitive_normals"].numpy()[mask]
        flip = (normals * rays[mask]).sum(axis=-1) > 0
        normals[flip] = -normals[flip]

        points = points[mask] + t_hit[mask, None] * rays[mask]

        surface_points.append(points)
        surface_normals.append(normals)

surface_points = np.concatenate(surface_points)
surface_normals = np.concatenate(surface_normals)

## Sample Point On The Surface

In [141]:
# sample the normals and points
num_point_cloud = 500000
random_mask = np.random.choice(surface_points.shape[0], num_point_cloud)
cloud_points = surface_points[random_mask]
cloud_normals = surface_normals[random_mask]

# build the point cloud and the KDTree
tree = KDTree(cloud_points, leaf_size=2) 

### Sample From Surface

In [ ]:
num_samples = 50000 
samples_mask = np.random.choice(cloud_points.shape[0], num_samples)
points = cloud_points[samples_mask]
sdfs = np.zeros(points.shape[0])
visualize_cloud(points, sdfs)

### Near Surface

In [142]:
def calculate_sdf(points: np.ndarray):
    sdfs, idx = tree.query(points, k=1)
    nearest_point = cloud_points[idx.squeeze()]
    nearest_normal = cloud_normals[idx.squeeze()]

    flip_mask = np.sum((points - nearest_point) * nearest_normal, axis=-1) < 0
    sdfs[flip_mask] = -sdfs[flip_mask]
    sdfs = sdfs.squeeze()

    return sdfs


def sample_near_surface(
    num_samples: int = 10000,
    inside_surface: bool = True,
    buffer_multiplier: float = 1.0,
    delta_mean: float = 0.0,
    delta_var: float = 5e-02,
):
    assert buffer_multiplier >= 1.0
    num_query_samples = int(num_samples * buffer_multiplier)
    mask = np.random.choice(cloud_points.shape[0], num_query_samples)

    delta = np.abs(np.random.normal(delta_mean, delta_var, size=num_query_samples))
    if inside_surface:
        delta = -delta
    points = cloud_points[mask] + cloud_normals[mask] * delta[..., None]
    sdfs = calculate_sdf(points)

    valid_mask = sdfs < 0 if inside_surface else sdfs > 0 
    valid_mask &= (np.linalg.norm(points, axis=-1) <= 1.0)
    
    points, sdfs = points[valid_mask], sdfs[valid_mask]

    # ensures that you have the required points and sdfs with recursion
    if sdfs.shape[0] < num_samples:
        points, sdfs = sample_near_surface(
            num_samples=num_samples,
            inside_surface=inside_surface,
            buffer_multiplier=buffer_multiplier*2,
            delta_mean=delta_mean,
            delta_var=delta_var
        )

    final_mask = np.random.choice(points.shape[0], num_samples)
    return points[final_mask], sdfs[final_mask]
    
neg_points, neg_sdfs = sample_near_surface(buffer_multiplier=1.5)
pos_points, pos_sdfs = sample_near_surface(buffer_multiplier=1.2, inside_surface=False)
points = np.concatenate([neg_points, pos_points])
sdfs = np.concatenate([neg_sdfs, pos_sdfs])
visualize_cloud(points, sdfs)

### Unit Ball Sample 

In [147]:
def calculate_sdf(points: np.ndarray):
    sdfs, idx = tree.query(points, k=1)
    nearest_point = cloud_points[idx.squeeze()]
    nearest_normal = cloud_normals[idx.squeeze()]

    flip_mask = np.sum((points - nearest_point) * nearest_normal, axis=-1) < 0
    sdfs[flip_mask] = -sdfs[flip_mask]
    sdfs = sdfs.squeeze()

    return sdfs

circle = o3d.geometry.TriangleMesh.create_sphere()
point_cloud = circle.sample_points_uniformly(number_of_points=20000)

points = np.asarray(point_cloud.points)
points = points / np.linalg.norm(points, axis=-1)[..., None]

# radius = np.random.uniform(size=points.shape[0])
radius = np.random.beta(2, 0.5, points.shape[0])
points = points * radius[..., None]

sdfs = calculate_sdf(points)
visualize_cloud(points, sdfs)

In [145]:
sdfs.max()

0.6763029552836887

In [ ]:
import matplotlib.pyplot as plt
alpha = 2
beta = 1
s = np.random.beta(alpha, beta, 1000)
count, bins, ignored = plt.hist(s, 30, density=True)
plt.show()

In [ ]:
s.max()